In [7]:
from bokeh.plotting import figure, output_notebook, show
from bokeh.palettes import brewer
from bokeh.io import export_svgs
import numpy as np
import json

import scipy
import scipy.stats
import pathlib

import os

os.environ['GILLESPIE'] = '/dev/shm/Git/Gillespie/cmake-build-release/Gillespie'

output_notebook()

Loading BokehJS ...

In [5]:
import analyzer

In [22]:
data = analyzer.load_trajectory(pathlib.Path('/data/response0.traj'))

loading /data/response0.traj


In [23]:
limit = 100000
x = np.delete(data['timestamps'], np.s_[limit:], axis=0)
y = np.delete(data['components'], np.s_[limit:], axis=1)

In [12]:
def log_likelihood(trajectory):
    reaction_events = np.array(trajectory['reaction_events'])
    concentrations = np.array(trajectory['components'])

    assert reaction_events.shape[0] == concentrations.shape[1]

    # for every reaction create an array that contains its propensity at every event
    reaction_propensities = []
    for reaction in trajectory['reactions']:
        # multiply reaction constant by the concentrations of the reactants
        propensity = reaction['k'] * np.prod([concentrations[x] for x in reaction['reactants']], axis=0)
        reaction_propensities.append(propensity)

    chosen_reaction_propensity = np.choose(reaction_events, reaction_propensities)

    # since the random variates are sampled according to the survival probability the following association is correct
    survival_probabilities = np.array(trajectory['random_variates'])

    piecewise_probabilities = chosen_reaction_propensity * survival_probabilities

    # log(product) => sum(log)
    return np.sum(np.log(piecewise_probabilities))

In [13]:
log_likelihood(data)

8178603.603329703

In [14]:
np.array(data["components"])

array([[1.00000000e+04, 1.00000000e+04, 1.00000000e+04, ...,
        1.07920575e+04, 1.07920575e+04, 1.07920575e+04],
       [1.01000000e+02, 1.02000000e+02, 1.03000000e+02, ...,
        1.94980000e+04, 1.94970000e+04, 1.94960000e+04],
       [0.00000000e+00, 0.00000000e+00, 0.00000000e+00, ...,
        4.90300000e+05, 4.90301000e+05, 4.90302000e+05]])

In [15]:
palette = brewer['Dark2'][8]

In [24]:
# create a new plot with a title and axis labels
p = figure(title="Trajectories", x_axis_label='t / s', y_axis_label='copies')

# add a line renderer with legend and line thickness
for y_value, col in zip(y, palette):
    p.step(x, y_value, line_width=2, color=col)

show(p)

In [ ]:
np.savetxt("tr2.txt", [x, y[1]])

In [ ]:
np.concatenate(([int_x], int_y), axis=0)

In [ ]:
p = figure()
p.line(int_x, int_y[0])
p.line(int_x, int_y[1])
show(p)

In [ ]:
hist = np.histogram(np.log(np.diff(txt_data[0])), bins='auto', density=True)
p=figure()
p.vbar(hist[1][:-1], width=np.diff(hist[1]), top=hist[0])
show(p)

In [ ]:
hist[0]

In [ ]:
np.loadtxt("tr2.txt").shape

In [ ]:
int_x

In [19]:
def ornstein_uhlenbeck_path(x0, t, mean_rev_speed, mean_rev_level, vola):
    """ Simulates a sample path for an Ornstein-Uhlenbeck process."""
    assert len(t) > 1
    x = scipy.stats.norm.rvs(size=len(t))
    x[0] = x0
    dt = np.diff(t)
    scale = std(dt, mean_rev_speed, vola)
    x[1:] = x[1:] * scale
    for i in range(1, len(x)):
        x[i] += mean(x[i - 1], dt[i - 1], mean_rev_speed, mean_rev_level)
    return x

def std(t, mean_rev_speed, vola):
    return np.sqrt(variance(t, mean_rev_speed, vola))

def variance(t, mean_rev_speed, vola):
    assert mean_rev_speed >= 0
    assert vola >= 0
    return vola * vola * (1.0 - np.exp(- 2.0 * mean_rev_speed * t)) / (2 * mean_rev_speed)

def mean(x0, t, mean_rev_speed, mean_rev_level):
    assert mean_rev_speed >= 0
    return x0 * np.exp(-mean_rev_speed * t) + (1.0 - np.exp(- mean_rev_speed * t)) * mean_rev_level

In [20]:
times = np.linspace(0, 100, 100000)
x = ornstein_uhlenbeck_path(10000, times, 0.001, 10000, 900)
p = figure()
p.line(times, x)
show(p)

In [27]:
json_obj = { 'timestamps': times.tolist(), 'components': [x.tolist()] }
with open("response/ouproc.txt", "w") as outfile:
    json.dump(json_obj, outfile)